# Managerial Decision Making and Modelling
by Daniele Barbato, Eleonora Marcassa, Manuel Trevisan

# Problem Statement
**Actv S.p.A.**, or **Azienda del Consorzio Trasporti Veneziano**, is an Italian public company operating under the coordination of Azienda Veneziana della Mobilità (AVM). The company manages the complete urban bus network in Venice, along with the tram network and navigation services.

This project is about on optimizing transportation connections on the sorroundings area of Mestre.

# System



## Collected data

- The company owns n. bus in total;
- In the considered area there are 853,761 inhabitants in the Metropolitan City of Venice;
- There are 704 bus routes in the considered area, taking in account that this number is comprheensive of round-trip lines;
- There are 1352 stops.


## Assumption
- The demand is proportionally distributed between the stops;
- 30s is the average time used to load people on the bus (da rivedere);
- A bus can make 3,5 km/l;
- The total cost for using a bus is around 2,00 €/km.
- Each bus can transport 100 people at a time
- The load factor is the 30% of the each bus capacity

##Elements

### Agents/DMs
- ACTV Agency is the only one decision maker;
- Each individual decide everyday if to take or not the bus.

### Entities
- Buses;
- Stops.

### Relstionships among elements
- The DM needs to determine the stops to be included in each route;
- The DM must allocate a specific number of buses to each trip based on the demand.
- The DM establishes a specific timetable for the journey to take place.

### Other costituents of the sysem
- The distance is not measured as the crow flies; buses must travel along roads and adhere to a precise route;
- Traffic congestion can lead to delays in travel time.
- Buses may encounter technical issues during the journey.






# Mathematical Model
## Parameters
- $S$: set of all stops
- $R$: set of all possible routes
- $c_r$: cost associated to the associated route $r \in R$

## Decision variables
- $y_{r}$: $ \begin{cases} 1 \text{ if the route \(r \in R\) is taken into account} \\ 0 \text{ otherwise}\end{cases}$


## Objective
The aim of this problem is to minimize the number of required routes to cover all stops within the considered area, while also minimizing the associated costs for each route.

$$min \sum_{r \in R} c_r y_r$$

## Constraints
| Constraints | Mathematical constraints|
|-----------|-----------|
|Each route can be fully activeted or not all activated|$y_r \in \left\{0,1\right\} \quad \forall r \in R$|
|Each stop must belong to at least one activated route|$\sum_{r\ni s}y_r \geq 1 \quad \forall s\in S $|




# Data Wrangling

In [1]:
# from google.colab import drive
# drive.mount('/content/drive')

In [2]:
import numpy as np
import pandas as pd
# !pip install seaborn
import seaborn as sns
# !pip install plotly.express
import plotly.express as px
# !pip install matplotlib.pyplot
import matplotlib.pyplot as plt
# !pip install folium
import folium
# !pip install pyomo
from pyomo.environ import *
# !apt-get install -y -qq coinor-cbc
# !pip install pyomo cplex
# import cplex
# !pip install pyomo neos
# import neos
# !pip install pyomo cbc
# import cbc
# !pip install gurobipy
import gurobipy

# !pip install sys
# import sys
# !pip install os
import os
os.environ["GRB_LICENSE_FILE"] = "C:/Users/megam/Documents/Gurobi/gurobi.lic"

# if 'google.colab' in sys.modules:
#   !pip install idaes-pse --pre
#   !idaes get-extensions --to ./bin
#   os.environ['PATH']+=':bin'

# os.environ['NEOS_EMAIL'] = 'obamba370@gmail.com'
# solver_manager = SolverManagerFactory('neos')
# instance = model.create_instance()
# results = solver_manager.solve(instance, opt='cplex', load_solutions=True)
# # ['bonmin', 'cbc', 'conopt', 'couenne', 'cplex', 'filmint', 'filter', 'ipopt', 'knitro', 'l-bfgs-b', 'lancelot', 'lgo', 'loqo', 'minlp', 'minos', 'minto', 'mosek', 'octeract', 'ooqp', 'path', 'raposa', 'snopt']
# (results)

C:\Users\megam\AppData\Local\Temp\ipykernel_7008\1763360713.py:2: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


## Agency

In [3]:
agency = []

with open("C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/agency.txt", "r") as file:
  for row in file:
    row_data = row.strip().split(',')
    agency.append(row_data)

column_names = ['agency_id', 'agency_name', 'agency_url', 'agency_timezone', 'agency_lang', 'agency_phone', 'agency_fare_url']

agency = pd.DataFrame(agency, columns = column_names)
agency = agency.drop(0)
agency

agency_id agency_name          agency_url agency_timezone agency_lang  \
1  ACTVs.p.a   ACTVs.p.a  http://www.actv.it     Europe/Rome          IT   

  agency_phone             agency_fare_url  
1    +39041041  http://www.veneziaunica.it

## Calendar
Weekly calendar in which a binary variable is used to assign the day to each service.

In [4]:
calendar = []

with open("C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/calendar.txt", "r") as file:
  for row in file:
    row_data = row.strip().split(',')
    calendar.append(row_data)

column_names = ['service_id', 'monday', 'tuesday', 'wednesday', 'thursday', 'friday', 'saturday', 'sunday', 'start_date', 'end_date']

calendar = pd.DataFrame(calendar, columns = column_names)
calendar = calendar.drop(0)
calendar = calendar.set_index(['start_date', 'end_date', 'service_id'])
calendar

monday tuesday wednesday thursday friday  \
start_date end_date service_id                                            
20240102   20240302 410209_000      0       0         0        0      0   
                    410208_000      0       0         0        1      0   
                    410205_000      1       0         0        0      1   
                    410206_000      0       1         0        0      0   
                    410207_000      0       0         1        0      0   
                    410210_000      0       0         0        0      0   

                               saturday sunday  
start_date end_date service_id                  
20240102   20240302 410209_000        1      0  
                    410208_000        0      0  
                    410205_000        0      0  
                    410206_000        0      0  
                    410207_000        0      0  
                    410210_000        0      1

In [5]:
calendar_dates = []

with open("C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/calendar_dates.txt", "r") as file:
  for row in file:
    row_data = row.strip().split(',')
    calendar_dates.append(row_data)

column_names = ['service_id', 'date', 'exception_type']
calendar_dates = pd.DataFrame(calendar_dates, columns = column_names)
calendar_dates = calendar_dates.drop(0)
calendar_dates = calendar_dates.set_index('service_id')
calendar_dates

date exception_type
service_id                         
410204_000  20240107              1
410210_000  20240107              2
410211_000  20240212              1
410205_000  20240212              2
410201_000  20240102              1
410206_000  20240102              2
410212_000  20240213              1
410206_000  20240213              2
410211_000  20240214              1
410207_000  20240214              2
410202_000  20240103              1
410207_000  20240103              2
410203_000  20240104              1
410208_000  20240104              2
410202_000  20240105              1
410205_000  20240105              2
410204_000  20240106              1
410209_000  20240106              2

## Shapes

In [6]:
shapes = []

with open("C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/shapes.txt", "r") as file:
  for row in file:
    row_data = row.strip().split(',')
    shapes.append(row_data)

column_names = ['shape_id', 'shape_pt_lat', 'shape_pt_lon', 'shape_pt_sequence', 'shape_dist_traveled']
shapes = pd.DataFrame(shapes, columns = column_names)
shapes = shapes.drop(0)
shapes["shape_pt_lat"] = shapes["shape_pt_lat"].astype(float)
shapes["shape_pt_lon"] = shapes["shape_pt_lon"].astype(float)
shapes["shape_pt_sequence"] = shapes["shape_pt_sequence"].astype(int)
shapes["shape_dist_traveled"] = shapes["shape_dist_traveled"].astype(float)
shapes = shapes.set_index('shape_id')
shapes

shape_pt_lat  shape_pt_lon  shape_pt_sequence  shape_dist_traveled
shape_id                                                                    
1_0_1        45.417820     12.368981                  0             0.000000
1_0_1        45.417545     12.368747                  1             0.035622
1_0_1        45.417423     12.368521                  2             0.058058
1_0_1        45.417377     12.368440                  3             0.066069
1_0_1        45.417259     12.368265                  4             0.084993
...                ...           ...                ...                  ...
5312_1_1     45.439953     12.313064                  6             0.445617
5312_1_1     45.439804     12.313172                  7             0.464518
5312_1_1     45.439587     12.313541                  8             0.502181
5312_1_1     45.439259     12.314774                  9             0.605032
5312_1_1     45.437889     12.317260                 10             0.851965

[646942 rows x 4 columns]

The different dataset used by ACTV Agency s.p.a. are imported below.

## Stops

In [7]:
stops_df = []

with open("C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/stops.txt", "r") as file:
  for row in file:
    row_data = row.strip().split(',')
    stops_df.append(row_data)

column_names = ['stop_id','stop_code', 'stop_name','stop_desc', 'stop_lat', 'stop_lon', 'zone_id','stop_url','location_type', 'parent_station', 'stop_timezone', 'wheelchair_boarding']

stops_df = pd.DataFrame(stops_df, columns = column_names)
stops_df = stops_df.drop(0)
stops_df = stops_df.drop("stop_code", axis = 1)
stops_df["stop_id"] = stops_df["stop_id"].astype(int)
stops_df = stops_df.set_index(["stop_name", "stop_id"])
stops_df = stops_df.drop(columns = ["stop_desc", "zone_id", "stop_url", "location_type", 'parent_station', 'stop_timezone', 'wheelchair_boarding'])
stops_df['stop_lat'] = stops_df['stop_lat'].astype(float)
stops_df['stop_lon'] = stops_df['stop_lon'].astype(float)
stops_df.head(10)

stop_lat   stop_lon
stop_name                 stop_id                      
Sottomarina Centro Anzian 3494     45.208572  12.292019
Sottomarina Tirreno       3495     45.208179  12.289858
Sottomarina Ionio         3496     45.205769  12.296965
Sottomarina Pisani        3498     45.203484  12.298001
Sottomarina Pegaso        3499     45.201317  12.299044
Sottomarina Vega          3500     45.199116  12.300149
Brondolo                  3501     45.184582  12.278887
Brondolo Foscarini        3502     45.181610  12.279794
                          3503     45.181622  12.279706
Via dei Cantieri Cantiere 3504     45.427792  12.257347

In [8]:
fig = px.scatter_mapbox(stops_df.reset_index(), lat='stop_lat', lon='stop_lon', zoom=10, hover_name='stop_name')

fig.update_layout(mapbox_style="open-street-map")

fig.show()

## Stop Times

In [9]:
stop_times = []

with open("C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/stop_times.txt", "r") as file:
  for row in file:
    row_data = row.strip().split(',')
    stop_times.append(row_data)

column_names = ['trip_id', 'arrival_time', 'departure_time', 'stop_id', 'stop_sequence', 'stop_headsign', 'pickup_type', 'drop_off_type', 'shape_dist_traveled']

stop_times = pd.DataFrame(stop_times, columns = column_names)
stop_times = stop_times.drop(0)
stop_times["stop_id"] = stop_times["stop_id"].astype(int)
stop_times['trip_id'] = stop_times['trip_id'].astype(int)
stop_times["stop_sequence"] = stop_times["stop_sequence"].astype(int)
stop_times = stop_times.set_index('trip_id')
stop_times = stop_times.drop('shape_dist_traveled', axis = 1)
stop_times

arrival_time departure_time  stop_id  stop_sequence stop_headsign  \
trip_id                                                                     
2           04:03:00       04:03:00     1485              1       VENEZIA   
2           04:03:00       04:03:00     1314              2       VENEZIA   
2           04:04:00       04:04:00     1315              3       VENEZIA   
2           04:06:00       04:06:00     1316              4       VENEZIA   
2           04:07:00       04:07:00     1326              5       VENEZIA   
...              ...            ...      ...            ...           ...   
41404       20:26:00       20:26:00     1477             38       TREVISO   
41404       20:27:00       20:27:00      663             39       TREVISO   
41404       20:28:00       20:28:00     1480             40       TREVISO   
41404       20:30:00       20:30:00      666             41       TREVISO   
41404       20:30:00       20:30:00     2749             42       TREVISO   

        pickup_type drop_off_type  
trip_id                            
2                 0             1  
2                 0             0  
2                 0             0  
2                 0             0  
2                 0             0  
...             ...           ...  
41404             0             0  
41404             0             0  
41404             0             0  
41404             0             0  
41404             1             0  

[1129619 rows x 7 columns]

## Routes

In [10]:
routes_df = []

with open("C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/routes.txt", "r") as file:
  for row in file:
    row_data = row.strip().split(',')
    routes_df.append(row_data)

column_names = ['route_id', 'agency_id', 'route_short_name', 'route_long_name','route_desc','route_type', 'route_url', 'route_color', 'route_text_color']

routes_df = pd.DataFrame(routes_df, columns=column_names)
routes_df = routes_df.drop(0)
routes_df = routes_df.set_index(["agency_id", 'route_short_name', 'route_long_name'])
routes_df["route_id"] = routes_df["route_id"].astype(int)
del routes_df["route_text_color"]
del routes_df["route_url"]
#routes_df["route_desc"].unique()
routes_df #faar svolare PM (people mover)

route_id  \
agency_id route_short_name route_long_name                                           
ACTVs.p.a 11               Santa Maria Elisabetta - Pellestrina Cimitero         1   
                           Santa Maria Elisabetta - Pellestrina Cimitero         2   
                           Santa Maria Elisabetta - Pellestrina Cimitero         3   
                           Malamocco Centro - Pellestrina Cimitero               4   
                           Santa Maria Del Mare - Pellestrina Cimitero           5   
...                                                                            ...   
          PK1              VENEZIA - Park Petroli                             1117   
                           Park Petroli - Tronchetto Tronchetto Fer           1118   
                           Park Petroli - VENEZIA                             1119   
          PM               Piazzale Roma - Tronchetto                         1120   
                           Tronchetto - Piazzale Roma                         1121   

                                                                         route_desc  \
agency_id route_short_name route_long_name                                            
ACTVs.p.a 11               Santa Maria Elisabetta - Pellestrina Cimitero         UL   
                           Santa Maria Elisabetta - Pellestrina Cimitero         UL   
                           Santa Maria Elisabetta - Pellestrina Cimitero         UL   
                           Malamocco Centro - Pellestrina Cimitero               UL   
                           Santa Maria Del Mare - Pellestrina Cimitero           UL   
...                                                                             ...   
          PK1              VENEZIA - Park Petroli                                UM   
                           Park Petroli - Tronchetto Tronchetto Fer              UM   
                           Park Petroli - VENEZIA                                UM   
          PM               Piazzale Roma - Tronchetto                            UM   
                           Tronchetto - Piazzale Roma                            UM   

                                                                         route_type  \
agency_id route_short_name route_long_name                                            
ACTVs.p.a 11               Santa Maria Elisabetta - Pellestrina Cimitero          3   
                           Santa Maria Elisabetta - Pellestrina Cimitero          3   
                           Santa Maria Elisabetta - Pellestrina Cimitero          3   
                           Malamocco Centro - Pellestrina Cimitero                3   
                           Santa Maria Del Mare - Pellestrina Cimitero            3   
...                                                                             ...   
          PK1              VENEZIA - Park Petroli                                 3   
                           Park Petroli - Tronchetto Tronchetto Fer               3   
                           Park Petroli - VENEZIA                                 3   
          PM               Piazzale Roma - Tronchetto                             3   
                           Tronchetto - Piazzale Roma                             3   

                                                                         route_color  
agency_id route_short_name route_long_name                                            
ACTVs.p.a 11               Santa Maria Elisabetta - Pellestrina Cimitero      5B5B5B  
                           Santa Maria Elisabetta - Pellestrina Cimitero      5B5B5B  
                           Santa Maria Elisabetta - Pellestrina Cimitero      5B5B5B  
                           Malamocco Centro - Pellestrina Cimitero            5B5B5B  
                           Santa Maria Del Mare - Pellestrina Cimitero        5B5B5B  
...                                                                              .

## Trips

In [11]:
trips = []

with open("C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/trips.txt", "r") as file:
  for row in file:
    row_data = row.strip().split(',')
    trips.append(row_data)

column_names = ['route_id', 'service_id', 'trip_id', 'trip_headsign', 'trip_short_name', 'direction_id', 'block_id', 'shape_id', 'wheelchair_accessible']

trips = pd.DataFrame(trips, columns = column_names)
trips = trips.drop(0)
trips["route_id"] = trips["route_id"].astype(int)
trips["trip_id"] = trips["trip_id"].astype(int)
trips = trips.set_index(['trip_headsign', 'route_id'])
trips = trips.drop(columns = ["wheelchair_accessible", "trip_short_name"])
trips

service_id  trip_id direction_id block_id  \
trip_headsign        route_id                                              
Pellestrina Cimitero 1         410204_000    23513            0   400111   
                     1         410204_000    23519            0   400111   
                     1         410204_000    23525            0   400111   
                     1         410204_000    23531            0   400111   
                     1         410204_000    23537            0   400111   
...                                   ...      ...          ...      ...   
Piazzale Roma        1121      410212_000    83828            1  1000002   
                     1121      410212_000    83830            1  1000002   
                     1121      410212_000    83832            1  1000002   
                     1121      410212_000    83834            1  1000002   
                     1121      410212_000    83836            1  1000002   

                               shape_id  
trip_headsign        route_id            
Pellestrina Cimitero 1            1_0_1  
                     1            1_0_1  
                     1            1_0_1  
                     1            1_0_1  
                     1            1_0_1  
...                                 ...  
Piazzale Roma        1121      5312_1_1  
                     1121      5312_1_1  
                     1121      5312_1_1  
                     1121      5312_1_1  
                     1121      5312_1_1  

[49415 rows x 5 columns]

## ACTV dataset

All the different dataset imported before (except for *Shapes*) are merged together to have a comprehensive view of the data.

In [12]:
#Creating a complete dataset
actv = trips.reset_index().merge(routes_df.reset_index(), on = ("route_id"))
actv = actv.merge(stop_times.reset_index(), on = ("trip_id"))
actv = actv.merge(stops_df.reset_index(), on = "stop_id")
actv = actv.merge(shapes.reset_index().drop(columns = ["shape_pt_lat", "shape_pt_lon"]).set_index("shape_id").groupby("shape_id").last(), on = "shape_id")

#Cleaning the new datset
actv = actv.drop(actv[(actv["route_desc"] == "UL") | (actv["route_desc"] == "UC") | (actv["route_desc"] == "ES") | (actv["route_short_name"] == "PM")].index)
actv = actv.set_index(["trip_id", "shape_id", "shape_dist_traveled", "route_long_name", "route_short_name", "route_id"])
actv = actv.sort_values(by = ["trip_id", "route_id", "stop_sequence"])
new_column_order = ["stop_id", "stop_name", "arrival_time", "departure_time", "stop_sequence", "direction_id", "pickup_type", "drop_off_type", "stop_lat", "stop_lon", "stop_headsign"]
actv = actv[new_column_order]
actv

stop_id  \
trip_id shape_id shape_dist_traveled route_long_name                 route_short_name route_id            
2       5084_1_1 15.376792           Risorgimento Miranese - VENEZIA 6                707          1485   
                                                                                      707          1314   
                                                                                      707          1315   
                                                                                      707          1316   
                                                                                      707          1326   
...                                                                                                 ...   
83851   5014_1_3 20.438244           MESTRE CENTRO B2 - Treviso      8E               156          1477   
                                                                                      156           663   
                                                                                      156          1480   
                                                                                      156           666   
                                                                                      156          2749   

                                                                                                            stop_name  \
trip_id shape_id shape_dist_traveled route_long_name                 route_short_name route_id                          
2       5084_1_1 15.376792           Risorgimento Miranese - VENEZIA 6                707       Risorgimento Miranese   
                                                                                      707        Miranese San Giorgio   
                                                                                      707            Trieste Miranese   
                                                                                      707             Trieste Robinie   
                                                                                      707              Trieste Catene   
...                                                                                                               ...   
83851   5014_1_3 20.438244           MESTRE CENTRO B2 - Treviso      8E               156         Treviso San Lazzaro   
                                                                                      156             Treviso Loredan   
                                                                                      156            Treviso San Zeno   
                                                                                      156                  Treviso FS   
                                                                                      156                     Treviso   

                                                                                               arrival_time  \
trip_id shape_id shape_dist_traveled route_long_name                 route_short_name route_id                
2       5084_1_1 15.376792           Risorgimento Miranese - VENEZIA 6                707          04:03:00   
                                                                                      707          04:03:00   
                                                                                      707          04:04:00   
                                                                                      707          04:06:00   
                                                                                      707          04:07:00   
...                                                                                                     ...   
83851   5014_1_3 20.438244           MESTRE CENTRO B2 - Treviso      8E               156          20:26:00   
                                                                                      156          20:27:00   
                    

In [13]:
# Creating a dataset with the cost per kilometer
Routes_costs = actv.reset_index()[["route_id", "shape_dist_traveled"]].drop_duplicates().reset_index(drop = True)
Kilometer_cost = 2
Routes_costs["route_cost"] = Routes_costs["shape_dist_traveled"]*Kilometer_cost
Routes_costs

route_id  shape_dist_traveled  route_cost
0         707            15.376792   30.753584
1         649            23.200928   46.401855
2         576            22.303180   44.606360
3         580            22.373652   44.747304
4         593            10.135664   20.271328
..        ...                  ...         ...
699       561             8.994231   17.988461
700       560            10.963288   21.926575
701       916            19.219748   38.439496
702       944            20.374805   40.749610
703       562             6.553367   13.106734

[704 rows x 3 columns]

In [14]:
#Creating a dataset for the mathematical model
for_model = actv.reset_index()[["route_id", "stop_id"]]
for_model = for_model.merge(Routes_costs[["route_id","route_cost"]], on = "route_id")

In [15]:
# Parameters
route_groups = for_model.groupby("route_id")
route_stops = route_groups["stop_id"].apply(list).to_dict()
route_costs = route_groups["route_cost"].first().to_dict()
stops = for_model["stop_id"].unique()
routes = list(route_stops.keys())

# Creating the model
model = ConcreteModel()

# Decision Variable
model.y = Var(routes, within=Binary)

# Model objective
model.obj = Objective(expr = sum(route_costs[route]*model.y[route] for route in routes), sense=minimize)

# Constraints
model.selection_constraint = ConstraintList()
for stop in stops:
      model.selection_constraint.add(sum(model.y[route] for route in route_stops if stop in route_stops[route])>=1)

# Solving
solver = SolverFactory('gurobi')
result = solver.solve(model)

# Results
print("Solver Status:", result.solver.status)

selected_routes = [route for route in routes if value(model.y[route]) == 1]
print("Number of Selected Routes:", len(selected_routes))
print("Selected Routes:", selected_routes)
total_cost = sum(route_costs[route] for route in selected_routes)
print("Total Cost:", total_cost)

Solver Status: ok
Number of Selected Routes: 110
Selected Routes: [39, 41, 42, 46, 47, 50, 56, 57, 60, 65, 67, 74, 77, 79, 81, 85, 90, 91, 92, 94, 96, 97, 98, 99, 102, 103, 105, 109, 110, 113, 121, 135, 144, 147, 154, 162, 166, 169, 171, 173, 528, 551, 555, 558, 573, 579, 584, 613, 629, 631, 645, 655, 657, 662, 677, 683, 685, 687, 694, 697, 717, 724, 730, 750, 763, 767, 768, 787, 795, 805, 811, 813, 815, 825, 839, 856, 858, 861, 892, 895, 897, 907, 911, 914, 925, 926, 940, 942, 949, 960, 961, 966, 971, 992, 993, 996, 1000, 1009, 1012, 1024, 1033, 1040, 1045, 1046, 1049, 1054, 1059, 1073, 1116, 1118]
Total Cost: 3140.8034317417337


# Commuters Section

In [16]:
comuni = pd.read_excel('C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/Codici Comuni italiani_1 gennaio 2011.xlsx', sheet_name = 1)
c = comuni.loc[comuni['Solo denominazione in italiano'] == 'Venezia']
c

Codice Regione  Codice Provincia  Codice Comune  \
8004               5                27             42   

      Codice Istat del Comune \n(formato alfanumerico)  \
8004                                             27042   

      Codice Istat del Comune \n(formato numerico)  \
8004                                         27042   

      Codice Istat del Comune a 103 province\n(formato numerico)  \
8004                                              27042            

      Codice Istat del Comune a 107 province\n(formato numerico)  \
8004                                              27042            

     Denominazione (italiano/tedesco) Solo denominazione in italiano  \
8004                          Venezia                        Venezia   

     Solo denominazione in tedesco  ...  Zona altimetrica  \
8004                           NaN  ...                 5   

      Altitudine del centro (metri)  Comune litoraneo  Comune Montano  \
8004                              2                 1              NM   

     Codice Sistema locale del lavoro 2001  \
8004                                   158   

      Denominazione Sistema locale del lavoro 2001  \
8004                                       VENEZIA   

     Superficie territoriale totale (kmq)  \
8004                               415.94   

      Popolazione legale 2001 (21/10/2001)  \
8004                                271073   

      Popolazione residente al 31/12/2008  Popolazione residente al 31/12/2009  
8004                               270098                               270801  

[1 rows x 21 columns]

**Variables Description**

- Record type
- Residence type
- Province of residence
- Municipality of residence
- Gender
- Reason for travel
- Place of study or work
- Province of habitual study or work
- Municipality of habitual study or work
- Foreign country of study or work
- Means
- Departure time
- Time taken
- Estimated number of individuals
- Number of individuals

In [17]:
def make_pend_matrix(path):
  import pandas as pd

  matrix = []
  with open(path, "r") as file:
    for row in file:
      row_data = row.strip().split()
      matrix.append(row_data)

  col_names = ["Tipo record","Tipo residenza", "Provincia di residenza", "Comune di residenza", "Sesso", "Motivo dello spostamento", "Luogo di studio o di lavoro",
              "Provincia abituale di studio o di lavoro", "Comune abituale di studio o di lavoro", "Stato estero di studio o di lavoro","Mezzo","Orario di uscita",
              "Tempo impiegato", "Stima numero di individui", "Numero di individui"]
  matrix = pd.DataFrame(matrix, columns=col_names)

  matrix = matrix.drop(columns = ["Tipo record", "Tipo residenza", "Sesso", "Motivo dello spostamento",
                                  "Stato estero di studio o di lavoro", "Orario di uscita", "Tempo impiegato"])
  matrix = matrix[matrix["Luogo di studio o di lavoro"] != "3"]

  for el in matrix.columns:
    try:
      matrix[el] = matrix[el].astype(int)
    except:
      continue

  matrix = matrix[matrix["Provincia di residenza"].isin([26, 27, 28])]
  matrix.reset_index(inplace = True, drop = True)
  return matrix

In [18]:
pend_mat = make_pend_matrix("C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/matrix_pendo2011_10112014.txt")
pend_mat

Provincia di residenza  Comune di residenza  \
0                           26                    1   
1                           26                    1   
2                           26                    1   
3                           26                    1   
4                           26                    1   
...                        ...                  ...   
278260                      28                   92   
278261                      28                   93   
278262                      28                   93   
278263                      28                   95   
278264                      28                  103   

        Luogo di studio o di lavoro  Provincia abituale di studio o di lavoro  \
0                                 1                                        26   
1                                 1                                        26   
2                                 1                                        26   
3                                 1                                        26   
4                                 1                                        26   
...                             ...                                       ...   
278260                            2                                        28   
278261                            1                                        28   
278262                            1                                        28   
278263                            1                                        28   
278264                            2                                        28   

        Comune abituale di studio o di lavoro Mezzo Stima numero di individui  \
0                                           1    04                0000001.00   
1                                           1    04                0000003.00   
2                                           1    04                0000002.00   
3                                           1    04                0000001.00   
4                                           1    05                0000001.00   
...                                       ...   ...                       ...   
278260                                     60     +                        ND   
278261                                     93     +                        ND   
278262                                     93     +                        ND   
278263                                     95     +                        ND   
278264                                     60     +                        ND   

       Numero di individui  
0                       ND  
1                       ND  
2                       ND  
3                       ND  
4                       ND  
...                    ...  
278260             0000002  
278261             0000001  
278262             0000001  
278263             0000001  
278264             0000001  

[278265 rows x 8 columns]

In [19]:
def pendcode_to_name(pend_mat):
  dic = {26: "Treviso", 27: "Venezia", 28: "Padova"}
  pend_mat["Provincia di residenza"] = pend_mat["Provincia di residenza"].map(dic)

  # Importing the file from which we look at the town code
  df_comuni = pd.read_excel("C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/Codici Comuni italiani_1 gennaio 2011.xlsx", sheet_name = 1)
  df_comuni = df_comuni[["Codice Provincia", "Codice Comune", "Solo denominazione in italiano"]]
  df_comuni = df_comuni[df_comuni["Codice Provincia"].isin([26, 27, 28])]
  df_comuni["Codice Provincia"] = df_comuni["Codice Provincia"].map(dic)

  #Cleaning and updating dataset
  pend_mat = pend_mat.merge(df_comuni,
                            left_on= ["Provincia di residenza", "Comune di residenza"],
                            right_on= ["Codice Provincia", "Codice Comune"],
                            how="left")
  pend_mat["Comune di residenza"] = pend_mat["Solo denominazione in italiano"]
  pend_mat = pend_mat.drop(columns= ["Solo denominazione in italiano", "Codice Comune", "Codice Provincia"])

  #Defining work places
  df_comuni = pd.read_excel("C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/Codici Comuni italiani_1 gennaio 2011.xlsx", sheet_name = 1)
  df_comuni = df_comuni[["Codice Provincia", "Codice Comune", "Solo denominazione in italiano", "Comune capoluogo di provincia", "Denominazione Sistema locale del lavoro 2001"]]
  df_comuni = df_comuni[df_comuni["Codice Provincia"].isin([ 26,  24,  28,  17,  22,  27,  25,  32,  93,  23,  30,  21,  18,
          15,  37,  34,  31,  29,  13,  98,  40,  38,  96,  39, 100,  57,
          41,  10,  33,  52,  48,  35,  12,  36,  50,  16,  19,  20,  45,
          14])]

  #Filtering
  selected_rows = df_comuni[df_comuni["Comune capoluogo di provincia"] == 1]
  dic_province = dict(zip(selected_rows["Codice Provincia"], selected_rows["Denominazione Sistema locale del lavoro 2001"]))


  #Replacing codes with names before merging
  pend_mat["Provincia abituale di studio o di lavoro"] = pend_mat["Provincia abituale di studio o di lavoro"].map(dic_province)
  df_comuni["Codice Provincia"] = df_comuni["Codice Provincia"].map(dic_province)

  #Keeping only columns of interest
  df_comuni = df_comuni[["Codice Provincia", "Codice Comune", "Solo denominazione in italiano"]]

  #Merging in order to update
  pend_mat = pd.merge(pend_mat, df_comuni, left_on=["Provincia abituale di studio o di lavoro", "Comune abituale di studio o di lavoro"], right_on=["Codice Provincia", "Codice Comune"], how="left")
  pend_mat["Comune abituale di studio o di lavoro"] = pend_mat["Solo denominazione in italiano"]

  #Dropping usless columns
  pend_mat = pend_mat.drop(columns=["Codice Provincia", "Codice Comune", "Solo denominazione in italiano"])

  return pend_mat

pend_mat = pendcode_to_name(pend_mat)

pend_mat

Provincia di residenza   Comune di residenza  \
0                     Treviso              Altivole   
1                     Treviso              Altivole   
2                     Treviso              Altivole   
3                     Treviso              Altivole   
4                     Treviso              Altivole   
...                       ...                   ...   
278260                 Padova             Torreglia   
278261                 Padova          Trebaseleghe   
278262                 Padova          Trebaseleghe   
278263                 Padova                Urbana   
278264                 Padova  Villafranca Padovana   

        Luogo di studio o di lavoro Provincia abituale di studio o di lavoro  \
0                                 1                                  TREVISO   
1                                 1                                  TREVISO   
2                                 1                                  TREVISO   
3                                 1                                  TREVISO   
4                                 1                                  TREVISO   
...                             ...                                      ...   
278260                            2                                   PADOVA   
278261                            1                                   PADOVA   
278262                            1                                   PADOVA   
278263                            1                                   PADOVA   
278264                            2                                   PADOVA   

       Comune abituale di studio o di lavoro Mezzo Stima numero di individui  \
0                                   Altivole    04                0000001.00   
1                                   Altivole    04                0000003.00   
2                                   Altivole    04                0000002.00   
3                                   Altivole    04                0000001.00   
4                                   Altivole    05                0000001.00   
...                                      ...   ...                       ...   
278260                                Padova     +                        ND   
278261                          Trebaseleghe     +                        ND   
278262                          Trebaseleghe     +                        ND   
278263                                Urbana     +                        ND   
278264                                Padova     +                        ND   

       Numero di individui  
0                       ND  
1                       ND  
2                       ND  
3                       ND  
4                       ND  
...                    ...  
278260             0000002  
278261             0000001  
278262             0000001  
278263             0000001  
278264             0000001  

[278265 rows x 8 columns]

In [20]:
com_str = "Arzergrande, Borgoricco, Campagna Lupia, Campolongo Maggiore, Camponogara, Casale sul Sile, Cavallino-Treporti, Cavarzere, Chioggia, Codevigo, Cona, Correzzola, Dolo, Fiesso d'Artico, Fossò, Marcon, Martellago, Mira, Mirano, Mogliano Veneto, Morgano, Noale, Noventa Padovana, Padova, Pianiga, Piove di Sacco, Pontelongo, Preganziol, Quarto d'Altino, Salzano, Santa Maria di Sala, Scorzè, Spinea, Stra, Trebaseleghe, Treviso, Vigonovo, Vigonza, Zero Branco, Venezia"
com_lst = com_str.split(", ")

pend_mat = pend_mat[pend_mat["Comune di residenza"].isin(com_lst)]
pend_mat = pend_mat[pend_mat["Comune abituale di studio o di lavoro"].isin(com_lst)]
pend_mat.reset_index(inplace = True, drop = True)

# Creating a single column containing the stima for those who have stima and Number for the others
pend_mat["numero"] = np.where(pend_mat["Numero di individui"] == "ND",
                              pend_mat["Stima numero di individui"],
                              pend_mat["Numero di individui"])

# Dropping old columns
pend_mat = pend_mat.drop(columns=["Stima numero di individui", "Numero di individui"])
# Changing the format
pend_mat["numero"] = pend_mat["numero"].astype(float)
pend_mat

Provincia di residenza Comune di residenza  Luogo di studio o di lavoro  \
0                    Treviso     Casale sul Sile                            1   
1                    Treviso     Casale sul Sile                            1   
2                    Treviso     Casale sul Sile                            1   
3                    Treviso     Casale sul Sile                            1   
4                    Treviso     Casale sul Sile                            1   
...                      ...                 ...                          ...   
39693                 Padova              Padova                            2   
39694                 Padova              Padova                            2   
39695                 Padova      Piove di Sacco                            1   
39696                 Padova        Trebaseleghe                            1   
39697                 Padova        Trebaseleghe                            1   

      Provincia abituale di studio o di lavoro  \
0                                      TREVISO   
1                                      TREVISO   
2                                      TREVISO   
3                                      TREVISO   
4                                      TREVISO   
...                                        ...   
39693                                   PADOVA   
39694                                   PADOVA   
39695                                   PADOVA   
39696                                   PADOVA   
39697                                   PADOVA   

      Comune abituale di studio o di lavoro Mezzo  numero  
0                           Casale sul Sile    04     1.0  
1                           Casale sul Sile    04     1.0  
2                           Casale sul Sile    04     3.0  
3                           Casale sul Sile    04     6.0  
4                           Casale sul Sile    04     1.0  
...                                     ...   ...     ...  
39693                      Noventa Padovana     +     2.0  
39694                               Vigonza     +     1.0  
39695                        Piove di Sacco     +     2.0  
39696                          Trebaseleghe     +     1.0  
39697                          Trebaseleghe     +     1.0  

[39698 rows x 7 columns]

In [21]:
#Creating a new dataset with the sum of numero for every row that has all equal values:
gr_pend_mat = pend_mat.groupby(['Provincia di residenza', 'Comune di residenza', 'Luogo di studio o di lavoro',
                                  'Provincia abituale di studio o di lavoro', 'Comune abituale di studio o di lavoro']).agg({'numero': 'sum'}).reset_index()
gr_pend_mat

Provincia di residenza Comune di residenza  Luogo di studio o di lavoro  \
0                    Padova         Arzergrande                            1   
1                    Padova         Arzergrande                            2   
2                    Padova         Arzergrande                            2   
3                    Padova         Arzergrande                            2   
4                    Padova         Arzergrande                            2   
...                     ...                 ...                          ...   
1305                Venezia            Vigonovo                            2   
1306                Venezia            Vigonovo                            2   
1307                Venezia            Vigonovo                            2   
1308                Venezia            Vigonovo                            2   
1309                Venezia            Vigonovo                            2   

     Provincia abituale di studio o di lavoro  \
0                                      PADOVA   
1                                      PADOVA   
2                                      PADOVA   
3                                      PADOVA   
4                                      PADOVA   
...                                       ...   
1305                                  VENEZIA   
1306                                  VENEZIA   
1307                                  VENEZIA   
1308                                  VENEZIA   
1309                                  VENEZIA   

     Comune abituale di studio o di lavoro  numero  
0                              Arzergrande  1532.0  
1                                 Codevigo   248.0  
2                               Correzzola    24.0  
3                         Noventa Padovana    24.0  
4                                   Padova   638.0  
...                                    ...     ...  
1305                   Santa Maria di Sala    58.0  
1306                                Scorzè    10.0  
1307                                Spinea   226.0  
1308                                  Stra   368.0  
1309                               Venezia   226.0  

[1310 rows x 6 columns]

## Google Maps Data

In [22]:
import lxml.etree

tree = lxml.etree.parse('C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/FERMATE_AUTOMOBILISTICHE_AVMACTV_1.kml')

res = []

fermate = tree.findall(".//{http://www.opengis.net/kml/2.2}Placemark")
#print("NOME FERMATA", ',', "COMUNE", sep='')
for fermata in fermate:
    name = fermata.find(".//{http://www.opengis.net/kml/2.2}name")
    extended_data = fermata.find(".//{http://www.opengis.net/kml/2.2}ExtendedData")
    if extended_data is not None:
        for data in extended_data.findall(".//{http://www.opengis.net/kml/2.2}Data"):
            if 'NOME FERMATA' in data.get('name'):
                nome2 = data.find(".//{http://www.opengis.net/kml/2.2}value").text
            if 'COMUNE' in data.get('name'):
                comune = data.find(".//{http://www.opengis.net/kml/2.2}value").text

    try:
        float(name.text)
    except:
        # print(name.text,',', comune, sep='')
        res.append({'name': name.text, 'comune': comune})
        continue

    try:
        float(nome2)
    except:
        # print(nome2, ',', comune, sep='')
        res.append({'name': nome2, 'comune': comune})
        continue

In [23]:
map = pd.read_csv("C:/Users/megam/OneDrive/unive/Magistrale/Second semester/Managerial Decision Making and Modelling/Project/Input_files/dataset.csv", encoding='latin-1')
map = map[["NOME FERMATA", "COMUNE"]].drop_duplicates().reset_index(drop = True)
map = map.rename(columns={"NOME FERMATA" : "stop_name"})

# Adding stops that were missing
stop_integration = {"Marcon Lombardi" : "Marcon",
             "Tito Selvanese" : "Venezia",
             "Maerne Rialto" : "Martellago",
             "Casino'" : "Venezia",
             "Ca' Noghera Casino'" : "Venezia",
             "Cercariolo della Resisten" : "Scorzè",
             "Provvisoria" : "Scorzè",
             "Quarto d'Altino Centro" : "Quarto d'Altino",
             "Quarto d'Altino Bellini" : "Quarto d'Altino",
             "Salzano Toscanigo" : "Salzano",
             "Spinea Zigaraga" : "Spinea",
             "Scorze' Cercariolo" : "Scorzè",
             "Quarto d'Altino Heraclia" : "Quarto d'Altino"}

new_rows = pd.DataFrame(stop_integration.items(), columns=['stop_name', 'COMUNE'])
map = pd.concat([map, new_rows], ignore_index=True)
map

stop_name           COMUNE
0       Madonna Marina Cimitero         Chioggia
1     Sottomarina Da Verrazzano         Chioggia
2          Sottomarina Calliope         Chioggia
3                  DISTR.METANO         Chioggia
4                 DISTR.GASOLIO         Chioggia
...                         ...              ...
1420    Quarto d'Altino Bellini  Quarto d'Altino
1421          Salzano Toscanigo          Salzano
1422            Spinea Zigaraga           Spinea
1423         Scorze' Cercariolo           Scorzè
1424   Quarto d'Altino Heraclia  Quarto d'Altino

[1425 rows x 2 columns]

## Fixing datasets according to purposes

In [24]:
# New dataset starting from actv
actv_for_model = actv.reset_index()[["route_id", "stop_id", "stop_sequence", "stop_name"]]
actv_for_model = actv_for_model.reset_index()
actv_for_model = actv_for_model.merge(map, on = "stop_name")
actv_for_model = actv_for_model.sort_values("index").drop_duplicates().drop(columns = "index").reset_index(drop = True)
actv_for_model = actv_for_model.merge(Routes_costs[["route_id","route_cost"]], on = "route_id")

# Fixing wrong town stops
actv_for_model.loc[actv_for_model["stop_id"] == 3370, "COMUNE"] = actv_for_model.loc[actv_for_model["stop_id"] == 3370, "COMUNE"].replace("Santa Maria di Sala", "Scorzè")
actv_for_model.loc[actv_for_model["stop_id"] == 3369, "COMUNE"] = actv_for_model.loc[actv_for_model["stop_id"] == 3369, "COMUNE"].replace("Santa Maria di Sala", "Scorzè")
actv_for_model.loc[actv_for_model["stop_id"] == 2880, "COMUNE"] = actv_for_model.loc[actv_for_model["stop_id"] == 2880, "COMUNE"].replace("Preganziol", "Mogliano Veneto")
actv_for_model.loc[actv_for_model["stop_id"] == 2881, "COMUNE"] = actv_for_model.loc[actv_for_model["stop_id"] == 2881, "COMUNE"].replace("Preganziol", "Mogliano Veneto")
actv_for_model.loc[actv_for_model["stop_id"] == 2706, "COMUNE"] = actv_for_model.loc[actv_for_model["stop_id"] == 2706, "COMUNE"].replace("Mogliano Veneto", "Preganziol")
actv_for_model.loc[actv_for_model["stop_id"] == 2707, "COMUNE"] = actv_for_model.loc[actv_for_model["stop_id"] == 2707, "COMUNE"].replace("Mogliano Veneto", "Preganziol")

actv_for_model.drop_duplicates(inplace = True)
actv_for_model.reset_index(inplace = True, drop = True)
actv_for_model["route_cost"] = actv_for_model["route_cost"].round(2)
actv_for_model

route_id  stop_id  stop_sequence                stop_name   COMUNE  \
0           707     1485              1    Risorgimento Miranese  Venezia   
1           707     1314              2     Miranese San Giorgio  Venezia   
2           707     1315              3         Trieste Miranese  Venezia   
3           707     1316              4          Trieste Robinie  Venezia   
4           707     1326              5           Trieste Catene  Venezia   
...         ...      ...            ...                      ...      ...   
17954       562     1011             11  Corso del Popolo Torino  Venezia   
17955       562      333             12        Durando Bellinato  Venezia   
17956       562      611             13        Giovannacci Ulloa  Venezia   
17957       562     6028             14         Lavelli Paolucci  Venezia   
17958       562     6037             15   Sant'Antonio Municipio  Venezia   

       route_cost  
0           30.75  
1           30.75  
2           30.75  
3           30.75  
4           30.75  
...           ...  
17954       13.11  
17955       13.11  
17956       13.11  
17957       13.11  
17958       13.11  

[17959 rows x 6 columns]

In [25]:
stops_ve = ["Liberta' Commercio", "Liberta' Fincantieri",
       "Liberta' Porto Marghera", "Liberta' Righi","Liberta' Santa Chiara", "VENEZIA", "Tronchetto", 'Tronchetto Mercato',
       'Tronchetto Tronchetto Fer', 'Tronchetto Vaporetti', "Piazzale Roma", "Corsia A7 Ve.Park", "VENEZIA CORSIA C", "Marittima (Cruise Terminal)",
       "Terminal Ro-Port"]

mask = (actv_for_model['COMUNE'] == 'Venezia') & (actv_for_model['stop_name'].isin(stops_ve))
actv_for_model.loc[mask, 'COMUNE'] = 'Venezia'

mask = ~actv_for_model['stop_name'].isin(stops_ve)
actv_for_model.loc[mask & (actv_for_model["COMUNE"] == "Venezia"), "COMUNE"] = "Mestre"
actv_for_model

route_id  stop_id  stop_sequence                stop_name  COMUNE  \
0           707     1485              1    Risorgimento Miranese  Mestre   
1           707     1314              2     Miranese San Giorgio  Mestre   
2           707     1315              3         Trieste Miranese  Mestre   
3           707     1316              4          Trieste Robinie  Mestre   
4           707     1326              5           Trieste Catene  Mestre   
...         ...      ...            ...                      ...     ...   
17954       562     1011             11  Corso del Popolo Torino  Mestre   
17955       562      333             12        Durando Bellinato  Mestre   
17956       562      611             13        Giovannacci Ulloa  Mestre   
17957       562     6028             14         Lavelli Paolucci  Mestre   
17958       562     6037             15   Sant'Antonio Municipio  Mestre   

       route_cost  
0           30.75  
1           30.75  
2           30.75  
3           30.75  
4           30.75  
...           ...  
17954       13.11  
17955       13.11  
17956       13.11  
17957       13.11  
17958       13.11  

[17959 rows x 6 columns]

In [26]:
# New dataset starting from gr_pend_mat
pend_mat_for_model = gr_pend_mat[["Comune di residenza", "Comune abituale di studio o di lavoro", "numero"]]
pend_mat_for_model

Comune di residenza Comune abituale di studio o di lavoro  numero
0            Arzergrande                           Arzergrande  1532.0
1            Arzergrande                              Codevigo   248.0
2            Arzergrande                            Correzzola    24.0
3            Arzergrande                      Noventa Padovana    24.0
4            Arzergrande                                Padova   638.0
...                  ...                                   ...     ...
1305            Vigonovo                   Santa Maria di Sala    58.0
1306            Vigonovo                                Scorzè    10.0
1307            Vigonovo                                Spinea   226.0
1308            Vigonovo                                  Stra   368.0
1309            Vigonovo                               Venezia   226.0

[1310 rows x 3 columns]

In [27]:
selected_rows = pend_mat_for_model.loc[pend_mat_for_model["Comune di residenza"] == "Venezia"].copy()
selected_rows["Comune di residenza"] = "Mestre"
selected_rows["numero"]  /= 3/2
pend_mat_for_model.loc[pend_mat_for_model["Comune di residenza"] == "Venezia", "numero"] /= 3/1
pend_mat_for_model = pd.concat([pend_mat_for_model, selected_rows], ignore_index = True)

In [28]:
selected_rows = pend_mat_for_model.loc[pend_mat_for_model["Comune abituale di studio o di lavoro"] == "Venezia"].copy()
selected_rows["Comune abituale di studio o di lavoro"] = "Mestre"
selected_rows["numero"]  /= 3/2
pend_mat_for_model.loc[pend_mat_for_model["Comune abituale di studio o di lavoro"] == "Venezia", "numero"] /= 3/1
pend_mat_for_model = pd.concat([pend_mat_for_model, selected_rows], ignore_index = True)

In [29]:
pend_mat_for_model

Comune di residenza Comune abituale di studio o di lavoro         numero
0            Arzergrande                           Arzergrande    1532.000000
1            Arzergrande                              Codevigo     248.000000
2            Arzergrande                            Correzzola      24.000000
3            Arzergrande                      Noventa Padovana      24.000000
4            Arzergrande                                Padova     638.000000
...                  ...                                   ...            ...
1385              Spinea                                Mestre    7600.966667
1386                Stra                                Mestre     262.666667
1387             Venezia                                Mestre   50028.613333
1388            Vigonovo                                Mestre     150.666667
1389              Mestre                                Mestre  100057.226667

[1390 rows x 3 columns]

In [30]:
## Per vedere quali fermate erano doppie in map
# seen = []
# dupl = []
# for i in range(len(map["stop_name"])):
#   if map["stop_name"][i] in seen:
#     dupl.append(map["stop_name"][i])
#   else:
#     seen.append(map["stop_name"][i])
# dupl

In [31]:
try:
  actv_for_model.set_index("route_id", inplace = True)
except:
  print("index is already set")

In [32]:
# Adding an ID to the demnand
pend_mat_for_model["demand_id"] = range(1, len(pend_mat_for_model)+1)

def add_id_prefix(number):
    return f"ID_{number}"

# Apply the function to the column
pend_mat_for_model['demand_id'] = pend_mat_for_model['demand_id'].apply(add_id_prefix)
pend_mat_for_model = pend_mat_for_model[["demand_id", "Comune di residenza",	"Comune abituale di studio o di lavoro",	"numero"]]
pend_mat_for_model

demand_id Comune di residenza Comune abituale di studio o di lavoro  \
0         ID_1         Arzergrande                           Arzergrande   
1         ID_2         Arzergrande                              Codevigo   
2         ID_3         Arzergrande                            Correzzola   
3         ID_4         Arzergrande                      Noventa Padovana   
4         ID_5         Arzergrande                                Padova   
...        ...                 ...                                   ...   
1385   ID_1386              Spinea                                Mestre   
1386   ID_1387                Stra                                Mestre   
1387   ID_1388             Venezia                                Mestre   
1388   ID_1389            Vigonovo                                Mestre   
1389   ID_1390              Mestre                                Mestre   

             numero  
0       1532.000000  
1        248.000000  
2         24.000000  
3         24.000000  
4        638.000000  
...             ...  
1385    7600.966667  
1386     262.666667  
1387   50028.613333  
1388     150.666667  
1389  100057.226667  

[1390 rows x 4 columns]

In [33]:
# # Creating a dictionary with all the lines that can satisfy each demand

# demand_dict = dict()
# demand_satisfied_by_route = dict()
# directly_unsatisfiable = []

# for i in range(len(pend_mat_for_model["Comune di residenza"])):                   # for each demand of travel
#   for el in actv_for_model.index.unique():                                        # for each route
#     Com_res = pend_mat_for_model.iloc[i]["Comune di residenza"]                   # saving the city of residence
#     Com_sw = pend_mat_for_model.iloc[i]["Comune abituale di studio o di lavoro"]  # saving the city of study/word
#     Line_com = actv_for_model.loc[el]["COMUNE"]                                   # saving the route

#     check1 = Com_res in list(Line_com)                                            # check if the city of residence is in the route
#     check2 = Com_sw in list(Line_com)                                             # check if the city of study/word is in the route

#     if check1 and check2:                                                         #if both checks are true
#       Stop_seq_res = actv_for_model.loc[el][actv_for_model.loc[el]['COMUNE'] == Com_res]["stop_sequence"].iloc[0] # saving the stop sequence city of residence
#       Stop_seq_sw = actv_for_model.loc[el][actv_for_model.loc[el]['COMUNE'] == Com_sw]["stop_sequence"].iloc[-1]  # saving the stop sequence city of study/word

#       check3 = Stop_seq_res < Stop_seq_sw                                         # check if the city of residence is touched before the city of study/word
#       if check3:
#         try:
#           demand_dict[pend_mat_for_model.iloc[i]["demand_id"]].append(el)         # append the route to the list correlated to the key rapresenting the demand if the list exist
#         except:
#           demand_dict[pend_mat_for_model.iloc[i]["demand_id"]] = [el]             # otherwise adds the route creating the list correlated to the key rapresenting the demand
#         try:
#           demand_satisfied_by_route[el].append(pend_mat_for_model.iloc[i]["demand_id"])    # append the key rapresenting the demand to the list correlated to the route if the list exist
#         except:
#           demand_satisfied_by_route[el] = [pend_mat_for_model.iloc[i]["demand_id"]]        # otherwise adds key rapresenting the demand creating the list correlated to the route
#         if pend_mat_for_model.iloc[i]["demand_id"] in direclty_unsatisfiable:
#           direclty_unsatisfiable.remove(pend_mat_for_model.iloc[i]["demand_id"])  # from now on I added some code to save demands that can't be stisfied with one route
#                                                                                   # (so thy don't have a route that goes frome the Com_res to the Com_sw)
#     else:
#       if pend_mat_for_model.iloc[i]["demand_id"] not in demand_dict.keys() and pend_mat_for_model.iloc[i]["demand_id"] not in direclty_unsatisfiable:
#         direclty_unsatisfiable.append(pend_mat_for_model.iloc[i]["demand_id"])

In [34]:
# Creating a dictionary with all the lines that can satisfy each demand and one with all the demands that can be satisfied by each line

# Preprocess actv_for_model to create a dictionary mapping each city to the routes that serve it
city_to_routes = {}
for el in actv_for_model.index.unique():
    Line_com = actv_for_model.loc[el]["COMUNE"]
    for city in Line_com:
        if city in city_to_routes:
            city_to_routes[city].append(el)
        else:
            city_to_routes[city] = [el]

# Initialize dictionaries
demand_dict = {}
demand_satisfied_by_route = {}
directly_unsatisfiable = []

# Iterate over groups
for (Com_res, Com_sw), group in pend_mat_for_model.groupby(["Comune di residenza", "Comune abituale di studio o di lavoro"]):
    # Get routes serving both residence and workplace cities
    routes_serving_cities = set(city_to_routes.get(Com_res, [])).intersection(city_to_routes.get(Com_sw, []))

    for route in routes_serving_cities:
        Stop_seq_res = actv_for_model.loc[route][actv_for_model.loc[route]['COMUNE'] == Com_res]["stop_sequence"].iloc[0]
        Stop_seq_sw = actv_for_model.loc[route][actv_for_model.loc[route]['COMUNE'] == Com_sw]["stop_sequence"].iloc[-1]

        if Stop_seq_res < Stop_seq_sw:
            demand_id = group["demand_id"].iloc[0]

            # Update demand_dict
            demand_dict.setdefault(demand_id, []).append(route)

            # Update demand_satisfied_by_route
            demand_satisfied_by_route.setdefault(route, []).append(demand_id)

            if demand_id in directly_unsatisfiable:
                directly_unsatisfiable.remove(demand_id)
    else:
        demand_id = group["demand_id"].iloc[0]
        if demand_id not in demand_dict and demand_id not in directly_unsatisfiable:
            directly_unsatisfiable.append(demand_id)

In [35]:
# Filtering only the pend. data that are stisfied by the actv
actv_pend_mat = pend_mat_for_model[~pend_mat_for_model["demand_id"].isin(directly_unsatisfiable)].reset_index(drop = True)
actv_pend_mat["numero"] = actv_pend_mat["numero"].astype(int)
actv_pend_mat

demand_id Comune di residenza Comune abituale di studio o di lavoro  \
0       ID_30          Borgoricco                            Borgoricco   
1       ID_51          Borgoricco                                Mirano   
2       ID_55          Borgoricco                   Santa Maria di Sala   
3      ID_259        Trebaseleghe                          Trebaseleghe   
4      ID_267        Trebaseleghe                       Mogliano Veneto   
..        ...                 ...                                   ...   
138   ID_1383             Salzano                                Mestre   
139   ID_1385              Scorzè                                Mestre   
140   ID_1386              Spinea                                Mestre   
141   ID_1388             Venezia                                Mestre   
142   ID_1390              Mestre                                Mestre   

     numero  
0      3786  
1       340  
2       328  
3      6950  
4       100  
..      ...  
138    2185  
139    2374  
140    7600  
141   50028  
142  100057  

[143 rows x 4 columns]

# Second Scenario
## Parameters
- $S$: set of all stops
- $R$: set of all possible routes
- $D$: set of all the demands from $i$ to $j$
- $c_r$: cost associated to the associated route $r \in R$
- $f_r$: fixed cost associated to each route $r \in R$
-  

## Decision variables
- $y_{r}$: $ \begin{cases} 1 \text{ if the route \(r \in R\) is taken into account} \\ 0 \text{ otherwise}\end{cases}$
- $x_r$: number of rides for each $r \in R$


## Objective
The aim of this problem is to minimize the number of required routes to cover all stops within the considered area, while also minimizing the associated costs for each route.

$$min \sum_{r \in R} c_rx_r+f_r y_r$$

## Constraints
| Constraints | Mathematical constraints|
|-----------|-----------|
|Each route can be fully activeted or not all activated|$y_r \in \left\{0,1\right\} \quad \forall r \in R$|
|Each stop must belong to at least one activated route|$\sum_{r\ni s}y_r \geq 1 \quad \forall s\in S $|
|Distributing passangers on routes |$d_{ij} \leq \sum_{r \in R} y_{ijr} \quad \forall i,j$|
|Buses' capacity must absorb all the passengers |$$\sum_{ij}\alpha_{ijr}y_{ijr} \leq qlx_r \quad \forall r \in R$$|
|The number of rides for each bus must not excees $M$|$x_r \leq My_r \quad \forall r \in R$|

In [36]:
import math
new_model = ConcreteModel()

# Paramteres
M = 32
alpha = 1/3
lf = 0.3
q = 100
C_f = 100
dx100 = 0.15

# Sets
route_groups = actv_for_model.groupby("route_id")
route_stops = route_groups["stop_id"].apply(list).to_dict()
route_costs = route_groups["route_cost"].first().to_dict()
stops = actv_for_model["stop_id"].unique()
routes = list(route_stops.keys())
demands = list(demand_dict.keys())
demand_dict
copy_actv_pend_mat = actv_pend_mat.copy()
copy_actv_pend_mat["numero"] = copy_actv_pend_mat["numero"].apply(lambda x: math.ceil(x * dx100))
demand_quant = copy_actv_pend_mat.set_index("demand_id")["numero"].to_dict()

# Decision variable
new_model.y = Var(routes, within=Binary)
new_model.x = Var(routes, domain=NonNegativeIntegers)
new_model.yijr = Var(routes, demands, domain=NonNegativeIntegers)

# Objective
new_model.obj = Objective(expr = sum(new_model.x[route]*route_costs[route] + C_f * new_model.y[route]for route in routes), sense = minimize)

# Constraints

new_model.demand_distribution_constraint = ConstraintList()
for demand in demands:
  new_model.demand_distribution_constraint.add(demand_quant[demand] <= sum(new_model.yijr[route, demand] for route in demand_dict[demand]))

new_model.rides_coverage_constraint = ConstraintList()
for route in routes:
  new_model.rides_coverage_constraint.add(sum(alpha * new_model.yijr[route, demand] for demand in demand_satisfied_by_route[route]) <= q * lf * new_model.x[route])

new_model.max_rides_contraint = ConstraintList()
for route in routes:
  new_model.max_rides_contraint.add(new_model.x[route] <= M*new_model.y[route])

#new_model.selection_constraint = ConstraintList()
#for stop in stops:
#    new_model.selection_constraint.add(sum(new_model.y[route] for route in route_stops if stop in route_stops[route])>=1)

# solver = SolverFactory('cbc')
# result = solver.solve(new_model)

# solver = SolverManagerFactory('neos',  tee=True, threads=20)
# result = solver.solve(new_model, opt='cplex')

# solver = SolverFactory('gurobi')
# result = solver.solve(new_model)

# # Results
# print("Solver Status:", result.solver.status)

# selected_routes = [route for route in routes if value(new_model.y[route]) == 1]
# non_selected_routes = [route for route in routes if value(new_model.y[route]) == 0]
# print("Number of Selected Routes:", len(selected_routes))
# print("Selected Routes:", selected_routes)
# route_rides = {}
# for route in selected_routes:
#   route_rides[route] = value(new_model.x[route])
#   #print(route_rides[route].key, ":", route_rides[route])
# print("Route rides: ", route_rides)
# print("Total Costs: ", new_model.obj())

## Deviding into ME-VE and others

### Routes in mestre-ve

In [98]:
actv_for_model_VE_ME = actv_for_model[actv_for_model["COMUNE"].isin(["Venezia", "Mestre"])]
routes_with_VE_ME = actv_for_model_VE_ME.reset_index()["route_id"].unique()
actv_for_model_VE_ME = actv_for_model.reset_index()[actv_for_model.reset_index()["route_id"].isin(routes_with_VE_ME)].set_index("route_id")
actv_for_model_VE_ME

stop_id  stop_sequence                stop_name  COMUNE  route_cost
route_id                                                                     
707          1485              1    Risorgimento Miranese  Mestre       30.75
707          1314              2     Miranese San Giorgio  Mestre       30.75
707          1315              3         Trieste Miranese  Mestre       30.75
707          1316              4          Trieste Robinie  Mestre       30.75
707          1326              5           Trieste Catene  Mestre       30.75
...           ...            ...                      ...     ...         ...
562          1011             11  Corso del Popolo Torino  Mestre       13.11
562           333             12        Durando Bellinato  Mestre       13.11
562           611             13        Giovannacci Ulloa  Mestre       13.11
562          6028             14         Lavelli Paolucci  Mestre       13.11
562          6037             15   Sant'Antonio Municipio  Mestre       13.11

[16190 rows x 5 columns]

In [99]:
actv_pend_mat_VE_ME = actv_pend_mat[actv_pend_mat["Comune di residenza"].isin(["Venezia", "Mestre"]) | actv_pend_mat["Comune abituale di studio o di lavoro"].isin(["Venezia", "Mestre"])]
actv_pend_mat_VE_ME.head()

demand_id Comune di residenza Comune abituale di studio o di lavoro  numero
22    ID_381     Mogliano Veneto                               Venezia    2710
30    ID_433          Preganziol                               Venezia     784
34    ID_463             Treviso                               Venezia    1121
44    ID_857              Marcon                               Venezia    2528
51    ID_892          Martellago                               Venezia    2959

In [100]:
# Preprocess actv_for_model to create a dictionary mapping each city to the routes that serve it
city_to_routes = {}
for el in actv_for_model_VE_ME.index.unique():
    Line_com = actv_for_model_VE_ME.loc[el]["COMUNE"]
    for city in Line_com:
        if city in city_to_routes:
            city_to_routes[city].append(el)
        else:
            city_to_routes[city] = [el]

# Initialize dictionaries
demand_dict = {}
demand_satisfied_by_route = {}
directly_unsatisfiable = []

# Iterate over groups
for (Com_res, Com_sw), group in actv_pend_mat_VE_ME.groupby(["Comune di residenza", "Comune abituale di studio o di lavoro"]):
    # Get routes serving both residence and workplace cities
    routes_serving_cities = set(city_to_routes.get(Com_res, [])).intersection(city_to_routes.get(Com_sw, []))

    for route in routes_serving_cities:
        Stop_seq_res = actv_for_model_VE_ME.loc[route][actv_for_model_VE_ME.loc[route]['COMUNE'] == Com_res]["stop_sequence"].iloc[0]
        Stop_seq_sw = actv_for_model_VE_ME.loc[route][actv_for_model_VE_ME.loc[route]['COMUNE'] == Com_sw]["stop_sequence"].iloc[-1]

        if Stop_seq_res < Stop_seq_sw:
            demand_id = group["demand_id"].iloc[0]

            # Update demand_dict
            demand_dict.setdefault(demand_id, []).append(route)

            # Update demand_satisfied_by_route
            demand_satisfied_by_route.setdefault(route, []).append(demand_id)

            if demand_id in directly_unsatisfiable:
                directly_unsatisfiable.remove(demand_id)
    else:
        demand_id = group["demand_id"].iloc[0]
        if demand_id not in demand_dict and demand_id not in directly_unsatisfiable:
            directly_unsatisfiable.append(demand_id)

In [101]:
import math
new_model_VE_ME = ConcreteModel()

# Paramteres
M = 50
alpha = 1/3
lf = 0.3
q = 100
C_f = 100
dx100 = 0.25
# Sets
route_groups = actv_for_model_VE_ME.groupby("route_id")
route_stops = route_groups["stop_id"].apply(list).to_dict()
route_costs = route_groups["route_cost"].first().to_dict()
stops = actv_for_model_VE_ME["stop_id"].unique()
routes = list(route_stops.keys())
demands = list(demand_dict.keys())
demand_dict
copy_actv_pend_mat = actv_pend_mat_VE_ME.copy()
copy_actv_pend_mat["numero"] = copy_actv_pend_mat["numero"].apply(lambda x: math.ceil(x * dx100))
demand_quant = copy_actv_pend_mat.set_index("demand_id")["numero"].to_dict()

# Decision variable
new_model_VE_ME.y = Var(routes, within=Binary)
new_model_VE_ME.x = Var(routes, domain=NonNegativeIntegers)
new_model_VE_ME.yijr = Var(routes, demands, domain=NonNegativeIntegers)

# Objective
new_model_VE_ME.obj = Objective(expr = sum(new_model_VE_ME.x[route]*route_costs[route] + C_f * new_model_VE_ME.y[route]for route in routes), sense = minimize)

# Constraints
new_model_VE_ME.demand_distribution_constraint = ConstraintList()
for demand in demands:
  new_model_VE_ME.demand_distribution_constraint.add(demand_quant[demand] <= sum(new_model_VE_ME.yijr[route, demand] for route in demand_dict[demand]))

new_model_VE_ME.rides_coverage_constraint = ConstraintList()
for route in routes:
  new_model_VE_ME.rides_coverage_constraint.add(sum(alpha * new_model_VE_ME.yijr[route, demand] for demand in demand_satisfied_by_route[route]) <= q * lf * new_model_VE_ME.x[route])

new_model_VE_ME.max_rides_contraint = ConstraintList()
for route in routes:
  new_model_VE_ME.max_rides_contraint.add(new_model_VE_ME.x[route] <= M*new_model_VE_ME.y[route])

#new_model_VE_ME.selection_constraint = ConstraintList()
#for stop in stops:
#    new_model_VE_ME.selection_constraint.add(sum(new_model_VE_ME.y[route] for route in route_stops if stop in route_stops[route])>=1)

# solver = SolverFactory('cbc')
# result = solver.solve(new_model_VE_ME)

# solver = SolverManagerFactory('neos',  tee=True, threads=20)
# result = solver.solve(new_model_VE_ME, opt='cplex')

solver = SolverFactory('gurobi')
result = solver.solve(new_model_VE_ME)

# Results
print("Solver Status:", result.solver.status)

selected_routes_VE_ME = [route for route in routes if value(new_model_VE_ME.y[route]) == 1]
non_selected_routes = [route for route in routes if value(new_model_VE_ME.y[route]) == 0]
print("Number of Selected Routes:", len(selected_routes_VE_ME))
print("Selected Routes:", selected_routes_VE_ME)
route_rides_VE_ME = {}
for route in selected_routes_VE_ME:
  route_rides_VE_ME[route] = value(new_model_VE_ME.x[route])
  #print(route_rides_VE_ME[route].key, ":", route_rides_VE_ME[route])
print("Route rides: ", route_rides_VE_ME)
print("Total Costs: ", new_model_VE_ME.obj())

Solver Status: ok
Number of Selected Routes: 35
Selected Routes: [45, 70, 82, 112, 115, 117, 124, 125, 127, 146, 148, 149, 153, 154, 161, 540, 541, 576, 580, 652, 656, 664, 666, 713, 815, 816, 861, 938, 943, 989, 990, 1070, 1117, 1118, 1119]
Route rides:  {45: 8.0, 70: 8.0, 82: 2.0, 112: 6.0, 115: 10.0, 117: 16.0, 124: 11.0, 125: 7.0, 127: 4.0, 146: 4.0, 148: 11.0, 149: 9.0, 153: 15.0, 154: 9.0, 161: 6.0, 540: 50.0, 541: 46.0, 576: 7.0, 580: 8.0, 652: 50.0, 656: 50.0, 664: 50.0, 666: 27.0, 713: 10.0, 815: 50.0, 816: 50.0, 861: 13.0, 938: 50.0, 943: 50.0, 989: 5.0, 990: 15.0, 1070: 21.0, 1117: 50.0, 1118: 50.0, 1119: 50.0}
Total Costs:  18215.43


## other routes

In [102]:
actv_for_model_others = actv_for_model[~actv_for_model["COMUNE"].isin(["Venezia", "Mestre"])]
other_routes = actv_for_model_others.reset_index()["route_id"].unique()
actv_for_model_others = actv_for_model.reset_index()[actv_for_model.reset_index()["route_id"].isin(other_routes)].set_index("route_id")
actv_for_model_others["COMUNE"].unique()

array(['Venezia', 'Mestre', 'Marcon', 'Martellago', 'Spinea',
       'Preganziol', 'Mogliano Veneto', 'Treviso', 'Scorzè', 'Salzano',
       'Noale', 'Mirano', 'Casale sul Sile', "Quarto d'Altino",
       'Santa Maria di Sala', 'Borgoricco', 'Zero Branco', 'Trebaseleghe',
       'Morgano', 'Mira'], dtype=object)

In [103]:
actv_pend_mat_others = actv_pend_mat[~actv_pend_mat["Comune di residenza"].isin(["Venezia", "Mestre"]) & ~actv_pend_mat["Comune abituale di studio o di lavoro"].isin(["Venezia", "Mestre"])]
actv_pend_mat_others

demand_id Comune di residenza Comune abituale di studio o di lavoro  \
0       ID_30          Borgoricco                            Borgoricco   
1       ID_51          Borgoricco                                Mirano   
2       ID_55          Borgoricco                   Santa Maria di Sala   
3      ID_259        Trebaseleghe                          Trebaseleghe   
4      ID_267        Trebaseleghe                       Mogliano Veneto   
..        ...                 ...                                   ...   
99    ID_1189              Spinea                            Martellago   
100   ID_1191              Spinea                                Mirano   
101   ID_1192              Spinea                                 Noale   
102   ID_1195              Spinea                               Salzano   
103   ID_1197              Spinea                                Scorzè   

     numero  
0      3786  
1       340  
2       328  
3      6950  
4       100  
..      ...  
99      527  
100    2363  
101     281  
102     206  
103     356  

[95 rows x 4 columns]

In [104]:
city_to_routes = {}
for el in actv_for_model_others.index.unique():
    Line_com = actv_for_model_others.loc[el]["COMUNE"]
    for city in Line_com:
        if city in city_to_routes:
            city_to_routes[city].append(el)
        else:
            city_to_routes[city] = [el]

# Initialize dictionaries
demand_dict = {}
demand_satisfied_by_route = {}
directly_unsatisfiable = []

# Iterate over groups
for (Com_res, Com_sw), group in actv_pend_mat_others.groupby(["Comune di residenza", "Comune abituale di studio o di lavoro"]):
    # Get routes serving both residence and workplace cities
    routes_serving_cities = set(city_to_routes.get(Com_res, [])).intersection(city_to_routes.get(Com_sw, []))

    for route in routes_serving_cities:
        Stop_seq_res = actv_for_model_others.loc[route][actv_for_model_others.loc[route]['COMUNE'] == Com_res]["stop_sequence"].iloc[0]
        Stop_seq_sw = actv_for_model_others.loc[route][actv_for_model_others.loc[route]['COMUNE'] == Com_sw]["stop_sequence"].iloc[-1]

        if Stop_seq_res < Stop_seq_sw:
            demand_id = group["demand_id"].iloc[0]

            # Update demand_dict
            demand_dict.setdefault(demand_id, []).append(route)

            # Update demand_satisfied_by_route
            demand_satisfied_by_route.setdefault(route, []).append(demand_id)

            if demand_id in directly_unsatisfiable:
                directly_unsatisfiable.remove(demand_id)
    else:
        demand_id = group["demand_id"].iloc[0]
        if demand_id not in demand_dict and demand_id not in directly_unsatisfiable:
            directly_unsatisfiable.append(demand_id)

In [105]:
import math
new_model_others = ConcreteModel()

# Paramteres
M = 50
alpha = 1/3
lf = 0.3
q = 100
C_f = 100
dx100 = 0.25

# Sets
route_groups = actv_for_model_others.groupby("route_id")
route_stops = route_groups["stop_id"].apply(list).to_dict()
route_costs = route_groups["route_cost"].first().to_dict()
stops = actv_for_model_others["stop_id"].unique()
routes = list(route_stops.keys())
demands = list(demand_dict.keys())
demand_dict
copy_actv_pend_mat = actv_pend_mat_others.copy()
copy_actv_pend_mat["numero"] = copy_actv_pend_mat["numero"].apply(lambda x: math.ceil(x * dx100))
demand_quant = copy_actv_pend_mat.set_index("demand_id")["numero"].to_dict()

# Decision variable
new_model_others.y = Var(routes, within=Binary)
new_model_others.x = Var(routes, domain=NonNegativeIntegers)
new_model_others.yijr = Var(routes, demands, domain=NonNegativeIntegers)

# Objective
new_model_others.obj = Objective(expr = sum(new_model_others.x[route]*route_costs[route] + C_f * new_model_others.y[route]for route in routes), sense = minimize)

# Constraints

new_model_others.demand_distribution_constraint = ConstraintList()
for demand in demands:
  new_model_others.demand_distribution_constraint.add(demand_quant[demand] <= sum(new_model_others.yijr[route, demand] for route in demand_dict[demand]))

new_model_others.rides_coverage_constraint = ConstraintList()
for route in routes:
  new_model_others.rides_coverage_constraint.add(sum(alpha * new_model_others.yijr[route, demand] for demand in demand_satisfied_by_route[route]) <= q * lf * new_model_others.x[route])

new_model_others.max_rides_contraint = ConstraintList()
for route in routes:
  new_model_others.max_rides_contraint.add(new_model_others.x[route] <= M*new_model_others.y[route])

#new_model_others.selection_constraint = ConstraintList()
#for stop in stops:
#    new_model_others.selection_constraint.add(sum(new_model_others.y[route] for route in route_stops if stop in route_stops[route])>=1)

# solver = SolverFactory('cbc')
# result = solver.solve(new_model_others)

# solver = SolverManagerFactory('neos',  tee=True, threads=20)
# result = solver.solve(new_model_others, opt='cplex')

solver = SolverFactory('gurobi')
result = solver.solve(new_model_others)

# Results
print("Solver Status:", result.solver.status)

selected_routes_others = [route for route in routes if value(new_model_others.y[route]) == 1]
non_selected_routes_others = [route for route in routes if value(new_model_others.y[route]) == 0]
print("Number of Selected Routes:", len(selected_routes_others))
print("Selected Routes:", selected_routes_others)
route_rides_others = {}
for route in selected_routes_others:
  route_rides_others[route] = value(new_model_others.x[route])
  #print(route_rides_others[route].key, ":", route_rides_others[route])
print("Route rides: ", route_rides_others)
print("Total Costs: ", new_model_others.obj())

Solver Status: ok
Number of Selected Routes: 38
Selected Routes: [39, 47, 50, 52, 56, 57, 59, 60, 65, 67, 70, 77, 81, 88, 91, 92, 97, 98, 99, 103, 104, 106, 109, 144, 145, 150, 151, 158, 160, 162, 167, 171, 172, 173, 640, 901, 1045, 1046]
Route rides:  {39: 48.0, 47: 6.0, 50: 3.0, 52: 2.0, 56: 4.0, 57: 6.0, 59: 8.0, 60: 4.0, 65: 4.0, 67: 2.0, 70: 5.0, 77: 14.0, 81: 6.0, 88: 17.0, 91: 21.0, 92: 2.0, 97: 2.0, 98: 22.0, 99: 2.0, 103: 2.0, 104: 31.0, 106: 15.0, 109: 39.0, 144: 7.0, 145: 34.0, 150: 16.0, 151: 50.0, 158: 50.0, 160: 50.0, 162: 49.0, 167: 23.0, 171: 6.0, 172: 16.0, 173: 2.0, 640: 22.0, 901: 25.0, 1045: 5.0, 1046: 4.0}
Total Costs:  17957.280000000002


In [106]:
selected_routes = selected_routes_VE_ME
for r in selected_routes_others:
    if r not in selected_routes:
        selected_routes.append(r)
print("Tot route selected: ", len(selected_routes))
print(selected_routes)

Tot route selected:  72
[45, 70, 82, 112, 115, 117, 124, 125, 127, 146, 148, 149, 153, 154, 161, 540, 541, 576, 580, 652, 656, 664, 666, 713, 815, 816, 861, 938, 943, 989, 990, 1070, 1117, 1118, 1119, 39, 47, 50, 52, 56, 57, 59, 60, 65, 67, 77, 81, 88, 91, 92, 97, 98, 99, 103, 104, 106, 109, 144, 145, 150, 151, 158, 160, 162, 167, 171, 172, 173, 640, 901, 1045, 1046]


In [111]:
route_rides = route_rides_VE_ME.copy()
for k,v in route_rides_others.items():
    if k not in route_rides.keys():
        route_rides[k] = v
    else:
        route_rides[k] = route_rides[k] + v

for k in route_rides.keys():
    if route_rides[k] > 32:
        print("Too high -> ",k ," : ", route_rides[k])
        
print("Sum of rides for route: ", route_rides)

Too high ->  540  :  50.0
Too high ->  541  :  46.0
Too high ->  652  :  50.0
Too high ->  656  :  50.0
Too high ->  664  :  50.0
Too high ->  815  :  50.0
Too high ->  816  :  50.0
Too high ->  938  :  50.0
Too high ->  943  :  50.0
Too high ->  1117  :  50.0
Too high ->  1118  :  50.0
Too high ->  1119  :  50.0
Too high ->  39  :  48.0
Too high ->  109  :  39.0
Too high ->  145  :  34.0
Too high ->  151  :  50.0
Too high ->  158  :  50.0
Too high ->  160  :  50.0
Too high ->  162  :  49.0
Sum of rides for route:  {45: 8.0, 70: 13.0, 82: 2.0, 112: 6.0, 115: 10.0, 117: 16.0, 124: 11.0, 125: 7.0, 127: 4.0, 146: 4.0, 148: 11.0, 149: 9.0, 153: 15.0, 154: 9.0, 161: 6.0, 540: 50.0, 541: 46.0, 576: 7.0, 580: 8.0, 652: 50.0, 656: 50.0, 664: 50.0, 666: 27.0, 713: 10.0, 815: 50.0, 816: 50.0, 861: 13.0, 938: 50.0, 943: 50.0, 989: 5.0, 990: 15.0, 1070: 21.0, 1117: 50.0, 1118: 50.0, 1119: 50.0, 39: 48.0, 47: 6.0, 50: 3.0, 52: 2.0, 56: 4.0, 57: 6.0, 59: 8.0, 60: 4.0, 65: 4.0, 67: 2.0, 77: 14.0, 81:

In [108]:
actv_sel = actv.reset_index()[actv.reset_index()["route_id"].isin(selected_routes)]

In [109]:
fig = px.scatter_mapbox(actv_sel, lat='stop_lat', lon='stop_lon', zoom=10, hover_name='stop_name')

fig.update_layout(mapbox_style="open-street-map")

fig.show()

In [110]:
for route in selected_routes:
  print("Route: ",route )
  for demand in demand_satisfied_by_route[route]:
    print("Demand: ", demand, ", yijr: ", value(new_model.yijr[route,demand]))

Route:  45
ERROR: evaluating object as numeric value: yijr[45,ID_859]
        (object: <class 'pyomo.core.base.var._GeneralVarData'>)
    No value for uninitialized NumericValue object yijr[45,ID_859]


ValueError: No value for uninitialized NumericValue object yijr[45,ID_859]

In [ ]:
for demand in demands:
  print("Demand: ",demand )
  for route in demand_dict[demand]:
    print("Route: ", route, ", yijr: ", value(new_model.yijr[route,demand]))